In [1]:
%matplotlib inline

import numpy as np
import matplotlib.pyplot as plt
from flowdec.nb import utils as nbutils 
from flowdec import data as fd_data
import pims
# import pims
from flowdec import restoration as fd_restoration
from flowdec import data as fd_data
from flowdec import psf as fd_psf
import dask
import dask.array as da
import tifffile as tf
# from nd2reader import ND2Reader
# from pims import ND2_Reader as ND2Reader
# import aicsimageio.vendor.omexml as ome
import glob
import time, sys
sys.path.insert(0,'./libraries/')
from deco_libraries import update_progress, pimsmeta2OMEXML, Nd2meta2OMEXML, observer, init_RL_algo, deconv, depth_divide

In [2]:
# channels = ['miRFP670', 'mRuby3','FITC']
import time, sys
from IPython.display import clear_output





In [55]:
#THINGS TO CHANGE!!!!! Always keep /*.nd2 at the end
#For gui make a function with all this input for verification purposes when loading the files
dirname = "/run/media/jmamede/Joao/anwar/*R3D.dv"

# dirname = "D:/JM/20201222caru3/Carubyigfp_F2_Nh4cl_vitc_rutin_BVD002.nd2"

filelist = glob.glob(dirname)
# filelist.pop()
# filelist = filelist[2:3]

print(filelist)

['/run/media/jmamede/Joao/anwar/20210716_D11_24N_NoIncubation_Opti01_04_R3D.dv', '/run/media/jmamede/Joao/anwar/20210804_D1_24N_MAS01_01_R3D.dv']


In [56]:
frames = pims.bioformats.BioformatsReader(filelist[0],java_memory='2048m')
print(frames.sizes)

metadata = frames.metadata
# print(metadata.ChannelEmissionWavelength(3,0))
print(frames.sizes)
#Grab metadata
metadata = frames.metadata
# print(metadata['channels'])

#If you don't have enough VRAM divide the XY to do the deconvolution that is automatically assembled after
xdivide = 1
ydivide = 1
depthdivide = depth_divide(xdivide, ydivide)

# frames.iter_axes = 't'  # 't' is the default already
# frames.bundle_axes = 'czyx' 

# frames[0]
filelist

{'x': 512, 'y': 512, 'c': 3, 't': 217, 'z': 22}
{'x': 512, 'y': 512, 'c': 3, 't': 217, 'z': 22}


/home/jmamede/anaconda3/lib/python3.7/site-packages/pims/bioformats.py:408: UserWarning: Due to an issue with JPype 0.6.0, reading is slower. Please consider upgrading JPype to 0.6.1 or later.
  warn('Due to an issue with JPype 0.6.0, reading is slower. '


['/run/media/jmamede/Joao/anwar/20210716_D11_24N_NoIncubation_Opti01_04_R3D.dv',
 '/run/media/jmamede/Joao/anwar/20210804_D1_24N_MAS01_01_R3D.dv']

In [5]:
frames.metadata.PixelsPhysicalSizeZ(0)

0.5

In [6]:
a = str(frames._metadata.dumpXML())

import aicsimageio.vendor.omexml as omexmlClass
b = omexmlClass.OMEXML(a)

In [7]:
b.to_xml()

'<?xml version=\'1.0\' encoding=\'utf-8\'?>\n<OME xmlns="http://www.openmicroscopy.org/Schemas/OME/2016-06" xmlns:xsi="http://www.w3.org/2001/XMLSchema-instance" UUID="urn:uuid:1397ef9e-d84a-43c0-acb9-b607925ee683" xsi:schemaLocation="http://www.openmicroscopy.org/Schemas/OME/2016-06 http://www.openmicroscopy.org/Schemas/OME/2016-06/ome.xsd"><Instrument ID="Instrument:0"><Objective Correction="PlanApo" ID="Objective:10612" Immersion="Oil" LensNA="1.42" Manufacturer="Olympus" Model="1-U2B933" NominalMagnification="60.0" WorkingDistance="0.15" WorkingDistanceUnit="mm" /></Instrument><Image ID="Image:0" Name="20210716_D11_24N_NoIncubation_Opti01_04_R3D.dv"><AcquisitionDate>1970-01-01T00:05:38</AcquisitionDate><Description>User: jmamede Host: cn63rt000337S Time: Fri Jul 16 13:03:28 2021</Description><InstrumentRef ID="Instrument:0" /><ObjectiveSettings ID="Objective:10612" /><Pixels BigEndian="false" DimensionOrder="XYZCT" ID="Pixels:0" Interleaved="false" PhysicalSizeX="0.2653999924659729

In [8]:
# xml = pimsmeta2OMEXML(frames, project=True,time_offset=0,verbose=False,maxT=None)
xml = pimsmeta2OMEXML(frames, project=False,time_offset=0,verbose=False,maxT=None)
xml.image().Pixels.PhysicalSizeZ

0.5

In [9]:
b.image().Pixels.PhysicalSizeZ

0.5

In [5]:

# #Need to make this a big more automatic, but indexing all the files and iterations is not easy
# #In the version where the PSF is estimated by flowdec is easier because everything was set to automatic

# PSFdir="/home/jmamede/Rush/PSF"
# # psf647 = tf.imread(PSFdir+"/AF647_0.3_EMCCD.tif")
# # psfruby =  tf.imread(PSFdir+'/mRuby3_0.3_EMCCD.tif')
# # psfgfp =  tf.imread(PSFdir+'/green_0.3_EMCCD.tif')
# # psfdapi =  tf.imread(PSFdir+'/DAPI_0.3_EMCCD.tif')
# psf647 = tf.imread(PSFdir+"/AF647_0.5_EMCCD.tif")
# psfruby =  tf.imread(PSFdir+'/mRuby3_0.5_EMCCD.tif')
# psfgfp =  tf.imread(PSFdir+'/green_0.5_EMCCD.tif')
# psfdapi =  tf.imread(PSFdir+'/DAPI_0.5_EMCCD.tif')
# # psf647 = tf.imread(PSFdir+"/AF647.tif")
# # psfruby =  tf.imread(PSFdir+'/mRuby3.tif')
# # psfgfp =  tf.imread(PSFdir+'/green.tif')
# # psfdapi =  tf.imread(PSFdir+'/DAPI.tif')
# # psfruby = psf647
# # psfgfp = psf647
# # psfdapi = psf647

# #Clip Top and bottom, I found that if the PSF is calculated with distance from coverslip, it is flipped from Fiji
# #As in, it is Top to Bottom, I acquire the images Bottom to Top
# remove = 8
# # remove = 14
# psf647 = np.flip(psf647,
# #                  axis=0
#                 )[remove:-remove]

# psfgfp = np.flip(psfgfp,
# #                  axis=0
#                 )[remove:-remove]
# psfdapi = np.flip(psfdapi,
# #                   axis=0
#                  )[remove:-remove]
# psfruby = np.flip(psfruby,
# #                   axis=0
#                  )[remove:-remove]

# print(psf647.shape)
# print(psfruby.shape)

TiffPage 0: TypeError: read_bytes() missing 3 required positional arguments: 'dtype', 'count', and 'offsetsize'
TiffPage 0: TypeError: read_bytes() missing 3 required positional arguments: 'dtype', 'count', and 'offsetsize'
TiffPage 0: TypeError: read_bytes() missing 3 required positional arguments: 'dtype', 'count', and 'offsetsize'
TiffPage 0: TypeError: read_bytes() missing 3 required positional arguments: 'dtype', 'count', and 'offsetsize'


(19, 128, 128)
(19, 128, 128)


In [52]:
metadata.ObjectiveAnnotationRefCount(0,0)

0

In [53]:
#Need to make this a big more automatic, but indexing all the files and iterations is not easy
#In the version where the PSF is estimated by flowdec is easier because everything was set to automatic


# na = meta['NA']
    
_ti0 =  metadata.ObjectiveWorkingDistance(0,0)*1000
mag = metadata.ObjectiveNominalMagnification(0,0)
metadata.ObjectiveWorkingDistance(0,0)*1000
na = metadata.ObjectiveLensNA(0,0)
#ra = meta['refractive_index1']
if metadata.ObjectiveImmersion(0,0) == 'Oil':
    ra = 1.5156
z = int(frames.sizes['z'])
z= 13
# z = 6
#     x = frames.sizes['x'] // 2
#     y = frames.sizes['y'] // 2
#     z = 26
x = 35
y = 35
res_z = xml.image().Pixels.PhysicalSizeZ
# res_z = xml.image().Pixels.PhysicalSizeZ
res_xy = xml.image().Pixels.PhysicalSizeX
# res_xy =  metadata['pixel_microns']
distance_cover = 0
##Make better with automatic wavelength from metadata and a loop and a dictionary with the PSFs
psf = fd_psf.GibsonLanni(
    na = na, wavelength= 0.670 , size_z=  z, size_x=  x , size_y=  y
    ,m = mag, ns =  1.333
    , tg =  170, tg0 = 170
    , ni0 =  ra, ni =  ra, ti0 = _ti0
    ,res_lateral =  res_xy , res_axial = res_z, 
    pz = distance_cover 
)
psf647 = psf.generate()    

psf = fd_psf.GibsonLanni(
    na = na, wavelength= 0.620 , size_z=  z, size_x=  x , size_y=  y
    ,m =mag, ns =  1.333
    , tg =  170, tg0 = 170
    , ni0 =  ra, ni =  ra, ti0 = _ti0
    ,res_lateral =  res_xy , res_axial = res_z, 
    pz = distance_cover 
)
psfruby = psf.generate()

psf = fd_psf.GibsonLanni(
    na = na, wavelength= 0.535 , size_z=  z, size_x=  x , size_y=  y
    ,m =mag, ns =  1.333
    , tg =  170, tg0 = 170
    , ni0 =  ra, ni =  ra, ti0 = _ti0
    ,res_lateral =  res_xy , res_axial = res_z, 
    pz = distance_cover 
)
psfgfp = psf.generate()

psf = fd_psf.GibsonLanni(
    na = na, wavelength= 0.420 , size_z=  z, size_x=  x , size_y=  y
    ,m =mag, ns =  1.333
    , tg =  170, tg0 = 170
    , ni0 =  ra, ni =  ra, ti0 = _ti0
    ,res_lateral =  res_xy , res_axial = res_z, 
    pz = distance_cover 
)
psfdapi = psf.generate()  

#Clip Top and bottom, I found that if the PSF is calculated with distance from coverslip, it is flipped from Fiji
#As in, it is Top to Bottom, I acquire the images Bottom to Top
# remove = 13
# remove = 14
# psf647 = np.flip(psf647,
# #                  axis=0
#                 )[remove:-remove]

# psfgfp = np.flip(psfgfp,
# #                  axis=0
#                 )[remove:-remove]
# psfdapi = np.flip(psfdapi,
# #                   axis=0
#                  )[remove:-remove]
# psfruby = np.flip(psfruby,
# #                   axis=0
#                  )[remove:-remove]

print(psf647.shape)
print(psfruby.shape)
# "C:/Users/Mamede/PSF/"

(13, 35, 35)
(13, 35, 35)


In [12]:
algo =init_RL_algo(psfgfp.ndim
                   ,pad_mode='2357',pad_min=(1,1,1)
                  )
filelist

['/run/media/jmamede/Joao/anwar/20210716_D11_24N_NoIncubation_Opti01_04_R3D.dv']

In [13]:
fname2 = filelist[1]
fname1 = filelist[0]
# frames.parser._raw_metadata.image_metadata
def get_deltaT(filename1,filename2):
    
    import pathlib

    fname1 = pathlib.Path(filename1)
    fname2 = pathlib.Path(filename2)
    import datetime
    mtime2 = datetime.datetime.fromtimestamp(fname2.stat().st_ctime)
    mtime1 = datetime.datetime.fromtimestamp(fname1.stat().st_ctime)
#     print(mtime2,mtime1)
#     print(fname2.stat().st_ctime - fname1.stat().st_ctime)
    return fname2.stat().st_ctime - fname1.stat().st_ctime
    # time_offset = 71146.03463482857
    
print(get_deltaT(fname1,fname2)/60)

time_offset = get_deltaT(fname1,fname2)
frames.metadata.ChannelCount(0)

IndexError: list index out of range

In [18]:
metadata.PlaneDeltaT(0,9)
metadata.PlaneDeltaT(0,9)


#       print(pixel.Plane(counter).PositionZ)
# prjxml = pimsmeta2OMEXML(frames, project=True,time_offset=0,verbose=False,maxT=None)
xml = omexmlClass.OMEXML(str(frames._metadata.dumpXML()))
prjxml = pimsmeta2OMEXML(frames, project=True,time_offset=time_offset,maxT=maxT,verbose=False)



217


In [22]:
frames.metadata.ChannelCount(0)
[frames.metadata.ChannelName(0,ch) for ch in range(frames.metadata.ChannelCount(0))]

AttributeError: 'MetadataRetrieve' object has no attribute 'ChannelName'

In [25]:
frames.metadata.ChannelID(0,0)

'Channel:0:0'

In [57]:
import aicsimageio.vendor.omexml as omexmlClass


savePRJ = True
saveStack = False
maxT = None
# time_offset = 0
concattime = False
for fname in filelist:
    #to add the real time of experiment when we have to split it into different files
    if concattime:
        time_offset = get_deltaT(fname1,fname)
    else: time_offset = 0
    frames =  pims.bioformats.BioformatsReader(fname,java_memory='1024m')
#     frames.iter_axes = 't'  # 't' is the default already
    frames.bundle_axes = 'zyx'  # when 'z' is available, this will be default

#     channels = [frames.metadata.ChannelEmissionWavelength(0,ch) for ch in range(frames.metadata.ChannelCount(0))]
    try:
        channels = [frames.metadata.ChannelName(0,ch) for ch in range(frames.metadata.ChannelCount(0))]
    except: channels = [frames.metadata.ChannelID(0,ch) for ch in range(frames.metadata.ChannelCount(0))]
    metadata = frames.metadata
    
    if saveStack:
#         xml = pimsmeta2OMEXML(frames,time_offset=time_offset,maxT=maxT)
        xml = omexmlClass.OMEXML(str(frames._metadata.dumpXML()))
    if savePRJ:
        prjxml = pimsmeta2OMEXML(frames, project=True,time_offset=time_offset,maxT=maxT,verbose=False)


#     psf =[]

    chunk_size=(frames.sizes['z'],frames.sizes['y']//ydivide,frames.sizes['x']//xdivide)


    # frames.iter_axes = 'v'
    # for frame in frames:
    #update SERIES HERE
    nseries = metadata.ImageCount()
    for visit in range(nseries):
#     for visit in range(21,31):

        frames.series = visit
        stackfile = fname[:-4]+"_v"+str(visit+1).zfill(2)+'.tiff'
        prjfile = fname[:-4]+"_v"+str(visit+1).zfill(2)+'_PRJ.ome.tiff'
        prjfile = fname.strip(".ome.tiff") +"_v"+str(visit+1).zfill(2)+'_PRJ.ome.tiff'
        if saveStack:
            tifstack = tf.TiffWriter(stackfile, bigtiff=False,imagej=False)
            firststk = True
        if savePRJ:
            tifprj = tf.TiffWriter(prjfile, bigtiff=False, imagej=False)
            first = True

        first = True
        if maxT == None:
            counterT = frames.sizes['t']
        else: counterT = maxT
        for time in range(counterT):
            res = np.zeros(
                (frames.sizes['z'],frames.sizes['c']
                 ,frames.sizes['y'],frames.sizes['x'])
                , dtype=np.float32)
            for i in range(frames.sizes['c']):
                frames.default_coords['c'] = i
#                     print('Channel:',metadata['channels'][i])
                ch = str(metadata.ChannelEmissionWavelength(0,i))
#                 ch = str(metadata.ChannelName(0,i))
                # ['a647', 'DAPI', 'GFP']
                # ['FITC', 'mRuby3', 'miRFP670']
                # ['FRET-gYFP-dsRED', 'mRuby', 'GFP', 'DAPI']
                # ['a647', 'DAPI', 'GFP']
                if ch == 'DAPI' or ch  == '470 nm':
                    psf = psfdapi
                elif ch == 'miRFP670' or ch == 'a647' or ch == 'mirfp670' or ch == 'farRED-EM':
                    psf = psf647
                elif ch == 'GFP' or ch == 'FITC'  or ch == 'GREEN-EM' or ch == 'FITC (Em)':
                    psf = psfgfp
                elif ch == 'mRuby3' or ch == 'mRuby' or ch ==  '555 nm' or ch == 'RED-EM':
                    psf = psfruby
                elif ch == 'FRET-gYFP-dsRED':
                    psf = psfruby
                elif ch == '548.0':
                    psf = psfyfp
                elif ch == '625.0' or ch == '626.0':
                    psf = psfch
                else: psf = psfruby

                arr = da.from_array(frames[time]
#                                     [:,0:2044,0:2044]
#                                     [:,:,:]              
                                    , chunks=chunk_size)

#                     print(arr.shape)
                res[:,i,:,:] = da.map_overlap(deconv,arr, depth  = depthdivide ,boundary='reflect',
                                    dtype='float32', algo=algo,
                                    psf=psf, iters=20
                                             ).compute(num_workers=1)
#                     res[:,i,:,:] = deconv(frames[time],
# #                                           depth  = depthdivide, boundary='reflect', dtype='float32',
#                                           algo=algo, psf=psf, iters=20
#                              )
#     .compute(num_workers=1)
                res[res> 2**16-1] = 2**16-1
                # res[i,:,:,:] = arr.map_blocks(
                # deconv,dtype='float32').compute(num_workers=1)

                # If we need to swap Channel and Z in the future
                #             img5d = np.swapaxes(img5d,0,1)

                update_progress( (visit+1) * (time+1) / (nseries * 
                                                         frames.sizes['t']
                                                        ) )
                print("Visit Point: {}/{} \t Time:{}/{} \t Channel:{}/{}".format(
                        visit+1, nseries,
                        time+1,
#                         1,
                        frames.sizes['t'],
                        i+1, frames.sizes['c']))

# Make Function

            if saveStack:

                if firststk:
                    tifstack.save(res.astype(np.uint16),
                        compression='ZLIB',
#                                   compression=9,
                        description = xml.to_xml(),
                        photometric='minisblack',
                        metadata= None,
                        contiguous=False
                        )
                    firststk = False

                else:
                    tifstack.save(res.astype(np.uint16),
                        compression='ZLIB',
#                                   compression=9,
#                         description = xml.to_xml(),
#                         datetime= True,
                        photometric='minisblack',
                        metadata= None,
                        contiguous=False
                        )
            if savePRJ:
                if first:
                    tifprj.save(res.astype(np.uint16).max(axis=0),
                        compression='ZLIB',
#                                 compression=9,
                        description = prjxml.to_xml(),
                        photometric='minisblack',
                        #, datetime= True
                        metadata= None,
                        contiguous=False
                        )
                    first = False
                else:                  
                    tifprj.save(res.astype(np.uint16).max(axis=0),
                        compression='ZLIB',
#                                 compression=9,
#                         description = xml.to_xml(),
                        photometric='minisblack',
                        #, datetime= True
                        metadata= None,
                        contiguous=False,
                        )
        if saveStack:
            tifstack.close()
        if savePRJ:
            tifprj.close()

    update_progress(1)

Progress: [####################] 100.0%


In [ ]:
# print('done')
from numba import cuda
cuda.select_device(0)
cuda.close()
#the memory was released here!
cuda.select_device(0)